In [3]:
import swifter
from compare_util import iterate_greedy, build_graph, compute_pagerank, iterate_pagerank, iterate_random
import networkx as nx
import operator
from random import *
import numpy as np

In [4]:
entity_types = set()
entities_cornell = []
sent_id = 0

files = ['/Users/grace/workspace/bio_dataset/CONLL2003/train.txt']

sents = []
for file_loc in files:
    f = open(file_loc, 'r')
    lines = f.readlines()[1:]

    sent = ''
    entities = []
    ent_types = []
    for l in lines:
        l = l.replace('\n', '')
        if l.strip():
            ll = l.split(' ')
            sent += ' '+ll[0]
            entity_types.add(ll[3])

            if ll[3].startswith('B'):
                entities.append(ll[0])
                ent_types.append(ll[3].replace('B-', ''))
            elif ll[3].startswith('I'):
                entities[len(entities)-1] = entities[len(entities)-1] + ' ' + ll[0]

            if ll[0]=='.':
                sents.append({'id':'cor_'+str(sent_id), 'sent':sent.strip()})
                sent = ''
                sent_id += 1
                entities_cornell.append({'id':'cor_'+str(sent_id), 'en_type':' *,* '.join(ent_types), 'en_val':' *,* '.join(entities)})

                entities = []
                ent_types = []

In [5]:
entity_types

{'B-LOC', 'B-MISC', 'B-ORG', 'B-PER', 'I-LOC', 'I-MISC', 'I-ORG', 'I-PER', 'O'}

In [6]:
df_sent_cornell = pd.DataFrame(sents)
df_sent_cornell.head()
df_sent_cornell.shape

id                                               sent
0  cor_0   EU rejects German call to boycott British lamb .
1  cor_1  Peter Blackburn BRUSSELS 1996-08-22 The Europe...
2  cor_2  Germany 's representative to the European Unio...
3  cor_3  " We do n't support any such recommendation be...
4  cor_4  He said further scientific study was required ...

(7374, 2)

In [7]:
df_cornell = pd.DataFrame(entities_cornell)
df_cornell.head()

en_type  \
0                  ORG *,* MISC *,* MISC   
1  PER *,* LOC *,* ORG *,* MISC *,* MISC   
2            LOC *,* ORG *,* PER *,* LOC   
3                            ORG *,* PER   
4                                    ORG   

                                              en_val     id  
0                          EU *,* German *,* British  cor_1  
1  Peter Blackburn *,* BRUSSELS *,* European Comm...  cor_2  
2  Germany *,* European Union *,* Werner Zwingman...  cor_3  
3                Commission *,* Nikolaus van der Pas  cor_4  
4                                     European Union  cor_5

In [8]:
cornell_entities = []
def reorganize_by_entity(row):
    val_list = list(filter(lambda x: x.strip(), row['en_val'].split(' *,* ')))
    cornell_entities.extend(list(map(lambda x:{'id':row['id'], 'val': x}, val_list)))

%time df_cornell.swifter.apply(reorganize_by_entity, axis=1)


CPU times: user 533 ms, sys: 22.9 ms, total: 556 ms
Wall time: 616 ms


0       None
1       None
2       None
3       None
4       None
5       None
6       None
7       None
8       None
9       None
        ... 
7364    None
7365    None
7366    None
7367    None
7368    None
7369    None
7370    None
7371    None
7372    None
7373    None
Length: 7374, dtype: object

In [9]:
df_cor_entities = pd.DataFrame(cornell_entities)
df_cor_entities.head()

id              val
0  cor_1               EU
1  cor_1           German
2  cor_1          British
3  cor_2  Peter Blackburn
4  cor_2         BRUSSELS

In [10]:
df_sorted = df_cor_entities.groupby(df_cor_entities.val).size().reset_index(name='count_').sort_values(['count_'], ascending=False)
df_sorted.head()

val  count_
7478       U.S.     330
1113    Britain     163
2752    Germany     162
643   Australia     154
2543     France     146

In [12]:
id_list = list(df_sent_cornell.id.unique())
for i in range(1):
    copy_cor_entities = df_cor_entities.copy(deep=True)
    
    print('greedy')
    no, ordered_ids = iterate_greedy(list(df_sorted.val.unique()), copy_cor_entities)
#     print('pagerank')    
#     iterate_pagerank(list(df_sorted.val.unique()), copy_cor_entities)
#     print('random')
#     iterate_random(list(df_sorted.val.unique()), df_cor_entities, id_list)

greedy


In [15]:
# ordered_ids[:1000]
ordered_ids[:5]

['cor_4936', 'cor_1052', 'cor_143', 'cor_108', 'cor_5433']

In [ ]:
sent_id = 0

files = ['/Users/grace/workspace/bio_dataset/CONLL2003/train.txt']
new_file = open('greedy_1000.txt', 'w')

sents = []
for file_loc in files:
    f = open(file_loc, 'r')ㅁㅊ
    lines = f.readlines()[1:]

    for line in lines:
        if 'cor_'+str(sent_id) in ordered_ids[:1000]:
            new_file.write(line)

        l = line.replace('\n', '')
        if l.strip():
            ll = l.split(' ')

            if ll[0]=='.':
                sent_id += 1

new_file.close()                

1

21

25

1

24

...

15

14

13

14

25